**<center><h1>T-SNE Notebook</h1></center>**

In [1]:
%load_ext autoreload
%autoreload 2
%matplotlib inline

In [2]:
import warnings
warnings.filterwarnings("ignore")

import pandas as pd
import matplotlib as mpl
import matplotlib.pyplot as plt
import numpy as np
import FenicsATL as FATL
from sklearn.cluster import KMeans
from sklearn.cluster import DBSCAN
from sklearn.manifold import TSNE

from multiprocessing import Process


Loading BokehJS ...

# **I. DATA INITIALIZATION**

I.2 FENICS 02

In [3]:
irrad = [106,107,108,109,110,116,117,118,119,120,126,127,128,129,130,136,137,138,139,140,1021,1022,1023,1024,1025,101,102,103,104,105,111,112,114,115,121,122,123,124,125,131,132,133,134,135]
LTT_id = [29,30,31,32,33,34,35,36,37,38,39,40,1041,1042,1043,1044,1045,1046,1047]
All = irrad + LTT_id

In [4]:
FENICS2 = FATL.FenicsVers_filter(FATL.FenicsData_read('/AtlasDisk/home2/sisaid/data/FENICS2_data.json'),All)

FastFeaturesToDrop = [("NoiseHG","Mean"),("NoiseHG","Mu"),
                      ("NoiseHGIG1","Mean"),("NoiseHGIG1","Mu"),
                      ("NoiseHGIG2","Mean"),("NoiseHGIG2","Mu"),
                      ("NoiseHGIG6","Mean"),("NoiseHGIG6","Mu"),
                      ("NoiseLG","Mean"),("NoiseLG","Mu"),
                      ("NoiseLGIG1","Mean"),("NoiseLGIG1","Mu"),
                      ("NoiseLGIG2","Mean"),("NoiseLGIG2","Mu"),
                      ("NoiseLGIG6","Mean"),("NoiseLGIG6","Mu")]

# FENICS2 = FENICS2[FENICS2.Board.burnTime.notna()]

# temp_allindex = []
# for id in FENICS2.Board.id.unique() :
#     temp_index = FENICS2[FENICS2.Board.id == id][FENICS2.Board.channel == FENICS2[FENICS2.Board.id == id].Board.channel.value_counts().index[0]].index.tolist()
#     temp_allindex = temp_allindex + temp_index
    
# FENICS2 = FENICS2.loc[temp_allindex]
FENICS2 = FENICS2[(FENICS2.Board.StatusFast != -1) | (FENICS2.Board.StatusSlow != -1)]

Fast2 = FATL.FenicsTestTable(FENICS2,'fast')
Slow2 = FATL.FenicsTestTable(FENICS2,'slow')


# Slow2 = FATL.Normalizer(Slow2)
# Fast2 = FATL.Normalizer(Fast2)

for feature in FastFeaturesToDrop:
    Fast2 = Fast2.drop(feature, axis=1) 

slow2_index = Slow2.index

Slow2.dropna(subset=[('Gain0','Linearity','SlopeLin'),('Gain1','Linearity','SlopeLin'),('Gain3','Linearity','SlopeLin'),('Gain4','Linearity','SlopeLin'),('Gain5','Linearity','SlopeLin'),
                     ('Gain0','Linearity','ConstLin'),('Gain1','Linearity','ConstLin'),('Gain3','Linearity','ConstLin'),('Gain4','Linearity','ConstLin'),('Gain5','Linearity','ConstLin'),], inplace=True)
Slow2.dropna(inplace=True,axis=1)
Fast2.drop(index=slow2_index.difference(Slow2.index), inplace=True)
FENICS2.drop(index=slow2_index.difference(Slow2.index), inplace=True)



FastSlow2 = pd.concat([Slow2, Fast2], axis=1)

In [5]:
FEN2_batch01_ids = [29,30,31,32,33,34,35,36,37,38,39,40]
FEN2_batch02_ids = [1041,1042,1043,1044,1045,1046,1047]
NIEL_ids = [101,102,103,104,105,111,112,114,115,121,122,123,124,125,131,132,133,134,135]
TID_ids = [106,107,108,109,110,116,117,118,119,120,126,127,128,129,130,136,137,138,139,140,1021,1022,1023,1024,1025]

AllFen2 = list(set(FENICS2.Board.id[(FENICS2.Board.StatusFast==0 ) | (FENICS2.Board.StatusSlow==0)])
               .union(
                set(FEN2_batch01_ids),
                set(FEN2_batch02_ids),
                set(NIEL_ids),
                set(TID_ids))
                )

AllFen2LTT = list(set(FEN2_batch01_ids).union(set(FEN2_batch02_ids)))


In [6]:
main_dir = '/users/divers/atlas/sisaid/home2/'

# **III. FENICS 2**

III.1 FENICS 02 : FAST DATA

In [7]:
tuples = [('Fast', 'NonNormed'),('Fast', 'Normed'),('Slow', 'NonNormed'),('Slow', 'Normed'),('FastSlow', 'NonNormed'),('FastSlow', 'Normed')]
mux = pd.MultiIndex.from_tuples(tuples)
Labels2 = pd.DataFrame(index=FENICS2.index,columns=mux)

In [8]:
CanalStatus = {
    'StatusSlow' : FENICS2.Board.StatusSlow,
    'StatusFast' :  FENICS2.Board.StatusFast
}

Normalization = {
    'NonNormed' : False,
    'Normed' : True,
                 }

# custom_filter = [('Combo',dict(labels_filter=irrad,
#                                 radio_categories=[dict(name = 'All',indexes=irrad),
#                                                     dict(name = 'TID',indexes=TID_ids),
#                                                     dict(name = 'NIEL',indexes=NIEL_ids),
#                                                     ]))]



custom_filter = [('Combo',dict(labels_filter=All,
                               slider_params=dict(step=20,title='burning'),
                               radio_categories=[dict(name='LTT',indexes=LTT_id),
                                                    dict(name = 'TID',indexes=TID_ids),
                                                    dict(name = 'NIEL',indexes=NIEL_ids),
                                                    ]))]


custom_filter_clusters = [('Combo',dict(labels_filter=All,
                               slider_params=dict(step=1,title='Clusters'),
                               radio_categories=[dict(name='LTT',indexes=LTT_id),
                                                    dict(name = 'TID',indexes=TID_ids),
                                                    dict(name = 'NIEL',indexes=NIEL_ids),
                                                    ]))]


for norm in Normalization.keys() :
    tsne_param = TSNE()
    tsne_param.fit(Fast2)

    tsne_bokeh = FATL.FenBokehTSNE(Fast2,normalize=Normalization[norm],perplexity=tsne_param.perplexity,n_iter=tsne_param.n_iter,learning_rate=tsne_param.learning_rate)

    OutputPath = main_dir+'fen2_output/t-sne/fast/HTML/'

    FATL.checkFolderAt(OutputPath)

    custom_filter = [('Combo',dict(labels_filter=irrad,radio_categories=[dict(name = 'All',indexes=irrad),dict(name = 'TID',indexes=TID_ids),dict(name = 'NIEL',indexes=NIEL_ids)]))]

    tsne= FATL.FenBokehGrapher(tsne_bokeh.tsne_x,tsne_bokeh.tsne_y,FENICS2.Board.version,FENICS2.Board.burnTime,FENICS2.Board.StatusFast,FENICS2.Board.StatusSlow,
                            colors=FENICS2.Board.burnTime ,labels=FENICS2.Board.id,
                            tooltips=[("card","FENICS02 @labels"),("burnTime","@burnTime"),
                                        ("StatusFast","@StatusFast"),("StatusSlow","@StatusSlow")])

    tsne.plotter(plotType='histogram',filters=custom_filter,
                title=f't-SNE : FENICS02 FAST; normed {tsne_bokeh.normed}; t-SNE params : perplexity={tsne_param.perplexity},n_iter={tsne_param.n_iter},learning_rate={tsne_param.learning_rate}')

    # tsne.save_as_html(path=OutputPath,filename=f'FEN2_FAST_t-SNE_perplexity_{tsne_param.perplexity}_wburn_normed_{tsne_bokeh.normed}.html')

    epsilon = 5
    min_samples = 2
    dbscan = DBSCAN(eps=epsilon, min_samples=min_samples)
    dbscan.fit(tsne_bokeh.embedding)

    Labels2[('Fast',norm)]= dbscan.labels_   

    Cluster_Filtred= FATL.FenBokehGrapher(tsne_bokeh.tsne_x,tsne_bokeh.tsne_y,
                                        colors=Labels2[('Fast',norm)] ,labels=FENICS2.Board.id,
                                        tooltips=[("card","FENICS02 @labels"),("Cluster","@colors")])

    Cluster_Filtred.plotter(plotType='histogram',filters=custom_filter_clusters,title='t-SNE : FENICS02 FAST (DBSCAN)')


    for status in CanalStatus.keys() :
        Cluster_Filtred= FATL.FenBokehGrapher(tsne_bokeh.tsne_x,tsne_bokeh.tsne_y,FENICS2.Board.version,FENICS2.Board.burnTime,FENICS2.Board.StatusFast,FENICS2.Board.StatusSlow,
                                            colors=CanalStatus[status] ,labels=FENICS2.Board.id,
                                            tooltips=[("card","FENICS02 @labels"),("burnTime","@burnTime"),
                                                        ("StatusFast","@StatusFast"),("StatusSlow","@StatusSlow")])

        Cluster_Filtred.plotter(plotType='histogram',filters=custom_filter,
                                title=f't-SNE : FENICS02 FAST (Fail : {status}); normed {tsne_bokeh.normed}; t-SNE params : perplexity={tsne_param.perplexity}')
        
        # Cluster_Filtred.save_as_html(path=OutputPath,filename=f'FEN2_FAST_t-SNE_perplexity_{tsne_param.perplexity}_wSStatusSlow_normed_{tsne_bokeh.normed}.html')


III.2 FENICS 02 : SLOW DATA

In [9]:
Slow2_filtred = pd.DataFrame()
Slow2_filtred = Slow2
removed_features_lienarity = ['DACforPed']
Slow2_filtred = Slow2_filtred.drop([('Gain0',   'NoisePhys'),('Gain1',  'NoisePhys'),
                                    ('Gain2',   'NoisePhys'),('Gain3',   'NoisePhys'),
                                    ('Gain4',   'NoisePhys'),('Gain5',  'NoisePhys')], axis=1) 

Slow2_filtred = Slow2_filtred.drop([('Gain0',   'NoisePosPed'),('Gain1',    'NoisePosPed'),
                                    ('Gain2',   'NoisePosPed'),('Gain3',   'NoisePosPed'),
                                    ('Gain4',   'NoisePosPed'),('Gain5',  'NoisePosPed')], axis=1) 

for feature in removed_features_lienarity :
    Slow2_filtred = Slow2_filtred.drop([('Gain0',   'Linearity',   feature),('Gain1',   'Linearity',    feature),
                                        ('Gain2',   'Linearity',    feature),('Gain3',   'Linearity',    feature),
                                        ('Gain4',   'Linearity',    feature),('Gain5',   'Linearity',    feature)], axis=1)

In [11]:
tsne_param = TSNE()
tsne_param.fit(Slow2_filtred)

for norm in Normalization.keys() :
    tsne_bokeh = FATL.FenBokehTSNE(Slow2_filtred,normalize=Normalization[norm],perplexity=tsne_param.perplexity,n_iter=tsne_param.n_iter,learning_rate=tsne_param.learning_rate)

    OutputPath = main_dir+'fen2_output/t-sne/slow/HTML/'

    FATL.checkFolderAt(OutputPath)

    tsne= FATL.FenBokehGrapher(tsne_bokeh.tsne_x,tsne_bokeh.tsne_y,FENICS2.Board.version,FENICS2.Board.burnTime,FENICS2.Board.StatusFast,FENICS2.Board.StatusSlow,
                            colors=FENICS2.Board.burnTime ,labels=FENICS2.Board.id,
                            tooltips=[("card","FENICS0@version @labels"),("burnTime","@burnTime"),
                                        ("StatusFast","@StatusFast"),("StatusSlow","@StatusSlow")])

    tsne.plotter(plotType='histogram',filters=custom_filter,
                title=f't-SNE : FENICS02 SLOW; normed {tsne_bokeh.normed}; t-SNE params : perplexity={tsne_param.perplexity},n_iter={tsne_param.n_iter},learning_rate={tsne_param.learning_rate}')

    # tsne.save_as_html(path=OutputPath,filename=f'FEN2_SLOW_t-SNE_perplexity_{tsne_param.perplexity}_wburn_normed_{tsne_bokeh.normed}.html')

    epsilon = 5
    min_samples = 2
    dbscan = DBSCAN(eps=epsilon, min_samples=min_samples)
    dbscan.fit(tsne_bokeh.embedding)

    Labels2[('Slow',norm)]= dbscan.labels_   

    Cluster_Filtred= FATL.FenBokehGrapher(tsne_bokeh.tsne_x,tsne_bokeh.tsne_y,
                                        colors=Labels2[('Slow',norm)] ,labels=FENICS2.Board.id,
                                        tooltips=[("card","FENICS02 @labels"),("Cluster","@colors")])

    Cluster_Filtred.plotter(plotType='histogram',filters=custom_filter_clusters,title='t-SNE : FENICS02 SLOW (DBSCAN)')

    
    
    
    for status in CanalStatus.keys() :
        Cluster_Filtred= FATL.FenBokehGrapher(tsne_bokeh.tsne_x,tsne_bokeh.tsne_y,FENICS2.Board.version,FENICS2.Board.burnTime,FENICS2.Board.StatusFast,FENICS2.Board.StatusSlow,
                                            colors=CanalStatus[status] ,labels=FENICS2.Board.id,
                                            tooltips=[("card","FENICS02 @labels"),("burnTime","@burnTime"),
                                                        ("StatusFast","@StatusFast"),("StatusSlow","@StatusSlow")])

        Cluster_Filtred.plotter(plotType='histogram',filters=custom_filter,
                                title=f't-SNE : FENICS02 SLOW (Fail : {status}); normed {tsne_bokeh.normed}; t-SNE params : perplexity={tsne_param.perplexity}')

        # Cluster_Filtred.save_as_html(path=OutputPath,filename=f'FEN2_SLOW_t-SNE_perplexity_{tsne_param.perplexity}_wStatusSlow_normed_{tsne_bokeh.normed}.html')
        

III.3 FENICS 02 : FAST + SLOW DATA

In [12]:
FastSlow2_filtred = pd.concat([Slow2_filtred, Fast2], axis=1)

In [14]:
tsne_param = TSNE()
tsne_param.fit(FastSlow2_filtred)

for norm in Normalization.keys() :
    tsne_bokeh = FATL.FenBokehTSNE(FastSlow2_filtred,normalize=Normalization[norm],perplexity=20,n_iter=200000,learning_rate=200)

    OutputPath = main_dir+'fen2_output/t-sne/fastslow/HTML/'

    FATL.checkFolderAt(OutputPath)


    tsne= FATL.FenBokehGrapher(tsne_bokeh.tsne_x,tsne_bokeh.tsne_y,FENICS2.Board.version,FENICS2.Board.burnTime,FENICS2.Board.StatusFast,FENICS2.Board.StatusSlow,
                            colors=FENICS2.Board.burnTime ,labels=FENICS2.Board.id,
                            tooltips=[("card","FENICS0@version @labels"),("burnTime","@burnTime"),
                                        ("StatusFast","@StatusFast"),("StatusSlow","@StatusSlow")])

    tsne.plotter(plotType='histogram',filters=custom_filter,
                title=f't-SNE : FENICS02 FAST + SLOW; normed {tsne_bokeh.normed}; t-SNE params : perplexity={tsne_param.perplexity},n_iter={tsne_param.n_iter},learning_rate={tsne_param.learning_rate}')

    # tsne.save_as_html(path=OutputPath,filename=f'FEN2_FASTSLOW_t-SNE_perplexity_{tsne_param.perplexity}_wburn_normed_{tsne_bokeh.normed}.html')

    epsilon = 5
    min_samples = 2
    dbscan = DBSCAN(eps=epsilon, min_samples=min_samples)
    dbscan.fit(tsne_bokeh.embedding)

    Labels2[('FastSlow',norm)]= dbscan.labels_   

    Cluster_Filtred= FATL.FenBokehGrapher(tsne_bokeh.tsne_x,tsne_bokeh.tsne_y,
                                        colors=Labels2[('FastSlow',norm)] ,labels=FENICS2.Board.id,
                                        tooltips=[("card","FENICS0@version @labels"),("Cluster","@colors")])

    Cluster_Filtred.plotter(plotType='histogram',filters=custom_filter_clusters,title='t-SNE : FENICS02 FastSlow (DBSCAN)')

    
    
    for status in CanalStatus.keys() :
        Cluster_Filtred= FATL.FenBokehGrapher(tsne_bokeh.tsne_x,tsne_bokeh.tsne_y,FENICS2.Board.version,FENICS2.Board.burnTime,FENICS2.Board.StatusFast,FENICS2.Board.StatusSlow,
                                            colors=CanalStatus[status] ,labels=FENICS2.Board.id,
                                            tooltips=[("card","FENICS0@version @labels"),("burnTime","@burnTime"),
                                                        ("StatusFast","@StatusFast"),("StatusSlow","@StatusSlow")])

        Cluster_Filtred.plotter(plotType='histogram',filters=custom_filter,
                                title=f't-SNE : FENICS02 Fast + SLOW (Fail : {status}); normed {tsne_bokeh.normed}; t-SNE params : perplexity={tsne_param.perplexity}')
        # Cluster_Filtred.save_as_html(path=OutputPath,filename=f'FEN2_FASTSLOW_t-SNE_perplexity_{tsne_param.perplexity}_wStatusSlow_normed_{tsne_bokeh.normed}.html')


# Clusters comparaison

In [ ]:
import pandas as pd

channels = ['Fast', 'Slow', 'FastSlow']
normali = ['NonNormed', 'Normed']

data = pd.concat([Slow2, Labels2, FENICS2.Board.StatusFast, FENICS2.Board.StatusSlow], axis=1)
dict = {}

for channel in channels:
    for norm in normali:
        groups = data.groupby((channel, norm))
        for group, indices in groups.groups.items():
            cluster_key = (channel, norm, 'Cluster ' + str(group))
            
            
            if (channel,norm,'Cluster '+ str(group)) not in dict:
                dict[(channel,norm,'Cluster '+ str(group))] = []
            
            cluster_data = data.loc[indices]
            cluster_count = len(cluster_data)
            cluster_failed_slow = cluster_data['StatusSlow'].value_counts().get(0, 0)
            cluster_failed_fast = cluster_data['StatusFast'].value_counts().get(0, 0)
            occurrences = FENICS2.Board.id.loc[indices].value_counts()

            
            dict[(channel,norm,'Cluster '+ str(group))].append(cluster_count)
            dict[(channel,norm,'Cluster '+ str(group))].append(cluster_failed_slow)
            dict[(channel,norm,'Cluster '+ str(group))].append(cluster_failed_slow / cluster_count * 100)
            dict[(channel,norm,'Cluster '+ str(group))].append(cluster_failed_fast)
            dict[(channel,norm,'Cluster '+ str(group))].append(cluster_failed_fast / cluster_count * 100)
            dict[(channel,norm,'Cluster '+ str(group))].append((occurrences.keys()[0], occurrences.iloc[0]))

            
            
            
failureByCluster = pd.DataFrame(dict,index=['group count','Slow fails','% Slow','Fast fails','% fast','id/Occurances'])

In [ ]:
failureByCluster

Fast                                                     \
              NonNormed                                   Normed             
              Cluster 0 Cluster 1 Cluster 2  Cluster 3 Cluster 0 Cluster 1   
group count        1428        26        13          2      1132       304   
Slow fails          207        24         1          0       205        16   
% Slow          14.4958   92.3077   7.69231          0   18.1095   5.26316   
Fast fails           31        15         0          0        31         8   
% fast          2.17087   57.6923         0          0   2.73852   2.63158   
id/Occurances  (40, 53)  (108, 2)   (33, 4)  (1045, 2)  (40, 53)  (29, 49)   

                                                        ...   FastSlow  \
                                                        ...     Normed   
              Cluster 2  Cluster 3 Cluster 4 Cluster 5  ... Cluster 26   
group count          12          7         2        10  ...         17   
Slow fails           11          0         0         0  ...         15   
% Slow          91.6667          0         0         0  ...    88.2353   
Fast fails            7          0         0         0  ...          1   
% fast          58.3333          0         0         0  ...    5.88235   
id/Occurances  (127, 1)  (1025, 7)   (30, 1)  (34, 10)  ...   (123, 6)   

                                                                      \
                                                                       
              Cluster 27 Cluster 28 Cluster 29 Cluster 30 Cluster 31   
group count            9          2         11         10         10   
Slow fails             4          0          0          0          0   
% Slow           44.4444          0          0          0          0   
Fast fails             0          0          0          0          0   
% fast                 0          0          0          0          0   
id/Occurances   (135, 9)    (30, 1)    (32, 9)   (34, 10)   (35, 10)   

                                                           
                                                           
              Cluster 32 Cluster 33 Cluster 34 Cluster 35  
group count            2          5          3          4  
Slow fails             0          0          0          0  
% Slow                 0          0          0          0  
Fast fails             0          0          0          0  
% fast                 0          0          0          0  
id/Occurances    (36, 2)    (36, 5)    (40, 2)  (1041, 4)  

[6 rows x 102 columns]

In [ ]:
high_failure_clusters = failureByCluster.loc[:, (failureByCluster.loc['% Slow'] > 20) & (failureByCluster.loc['% fast'] > 20)]

print(high_failure_clusters)


                   Fast             FastSlow
              NonNormed    Normed  NonNormed
              Cluster 1 Cluster 2  Cluster 7
group count          26        12         84
Slow fails           24        11         84
% Slow          92.3077   91.6667        100
Fast fails           15         7         26
% fast          57.6923   58.3333    30.9524
id/Occurances  (108, 2)  (127, 1)  (137, 13)


In [ ]:
import pandas as pd
import numpy as np
from scipy.stats import f_oneway

def perform_anova(df1, df2):
    combined_data = pd.concat([df1, df2], keys=['df1', 'df2'])

    groups = []
    for label in combined_data.index.unique():
        groups.append(combined_data.xs(label))

    f_statistic, p_value = f_oneway(*groups)
    
    
    return f_statistic, p_value


data = pd.concat([Slow2, Labels2, FENICS2.Board.StatusFast, FENICS2.Board.StatusSlow], axis=1)

channels = ['Fast', 'Slow', 'FastSlow']
normali = ['NonNormed', 'Normed']

dict = {}

for channel in channels:
    for norm in normali:
        groups = data.groupby(('Slow','Normed'))
        for ii in list(groups.groups.keys()) :
            for jj in list(groups.groups.keys()) :
                if (channel,norm,'Cluster '+str(ii),'Cluster '+str(jj)) not in dict:
                    dict[(channel,norm,'Cluster '+str(ii),'Cluster '+str(jj))] = []
                    
                f_statistic, p_value = perform_anova(groups.get_group(ii), groups.get_group(jj))
                dict[(channel,norm,'Cluster '+str(ii),'Cluster '+str(jj))].append(f_statistic)
                dict[(channel,norm,'Cluster '+str(ii),'Cluster '+str(jj))].append(p_value)
                
ANOVA_analysis = pd.DataFrame(dict,index=['f_statistic','p_value'])

In [ ]:
ANOVA_analysis

Fast                                              \
            NonNormed                                               
            Cluster 0                                               
            Cluster 0 Cluster 1     Cluster 2 Cluster 3 Cluster 4   
f_statistic  0.461683  0.427492  1.417396e+00  0.994168  0.571890   
p_value      1.000000  1.000000  4.931575e-09  0.507287  0.999997   

                                                                            \
                                                                             
                                                                             
                Cluster 5      Cluster 6 Cluster 7 Cluster 8     Cluster 9   
f_statistic  2.768485e+00   5.655320e+00  0.342365  0.484733  2.707637e+00   
p_value      3.962103e-31  2.063766e-135  1.000000  0.999996  3.495250e-22   

             ...   FastSlow                                                 \
             ...     Normed                                                  
             ... Cluster 17                                                  
             ...  Cluster 8     Cluster 9 Cluster 10 Cluster 11 Cluster 12   
f_statistic  ...   0.156804  3.379901e+00   0.034391   0.999151   0.122178   
p_value      ...   1.000000  1.092428e-20   1.000000   0.489371   1.000000   

                                                                       
                                                                       
                                                                       
               Cluster 13 Cluster 14 Cluster 15 Cluster 16 Cluster 17  
f_statistic  4.513694e+00    0.01303   0.005524   1.321606   0.001438  
p_value      3.346951e-60    1.00000   1.000000   0.074243   1.000000  

[2 rows x 1944 columns]

In [ ]:
high_failure_clusters = ANOVA_analysis.loc[:, (ANOVA_analysis.loc['f_statistic'] > 0.01) | (ANOVA_analysis.loc['p_value'] > 0.01)]
print(high_failure_clusters)


                 Fast                                              \
            NonNormed                                               
            Cluster 0                                               
            Cluster 0 Cluster 1     Cluster 2 Cluster 3 Cluster 4   
f_statistic  0.461683  0.427492  1.417396e+00  0.994168  0.571890   
p_value      1.000000  1.000000  4.931575e-09  0.507287  0.999997   

                                                                            \
                                                                             
                                                                             
                Cluster 5      Cluster 6 Cluster 7 Cluster 8     Cluster 9   
f_statistic  2.768485e+00   5.655320e+00  0.342365  0.484733  2.707637e+00   
p_value      3.962103e-31  2.063766e-135  1.000000  0.999996  3.495250e-22   

             ...   FastSlow                                                 \
             ...     Normed           